In [ ]:
!jupyter nbconvert --execute --to html "/content/Cosmos_Art_Project.ipynb"

[NbConvertApp] Converting notebook /content/Cosmos_Art_Project.ipynb to html
0.00s - Debugger warning: It seems that frozen modules are being used, which may
0.00s - make the debugger miss breakpoints. Please pass -Xfrozen_modules=off
0.00s - to python to disable frozen modules.
0.00s - Note: Debugging will proceed. Set PYDEVD_DISABLE_FILE_VALIDATION=1 to disable this validation.
0.00s - Debugger warning: It seems that frozen modules are being used, which may
0.00s - make the debugger miss breakpoints. Please pass -Xfrozen_modules=off
0.00s - to python to disable frozen modules.
0.00s - Note: Debugging will proceed. Set PYDEVD_DISABLE_FILE_VALIDATION=1 to disable this validation.
[NbConvertApp] Writing 300068 bytes to /content/Cosmos_Art_Project.html


In [2]:
import torch
import torch.nn as nn
import numpy as np
import cv2
from PIL import Image
import io
import ipywidgets as widgets
from IPython.display import display
import random

# Set random seeds for reproducibility
def set_seed(seed=42):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    if torch.cuda.is_available():
        torch.cuda.manual_seed_all(seed)
        torch.backends.cudnn.deterministic = True
        torch.backends.cudnn.benchmark = False

set_seed()

# Define the model architecture (must match training)
class PatchCraftDetector(nn.Module):
    def __init__(self, patch_size=64):
        super(PatchCraftDetector, self).__init__()
        self.features = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=3, padding=1),
            nn.ReLU(inplace=True),
            nn.MaxPool2d(2),
            nn.Conv2d(32, 64, kernel_size=3, padding=1),
            nn.ReLU(inplace=True),
            nn.MaxPool2d(2),
            nn.Conv2d(64, 128, kernel_size=3, padding=1),
            nn.ReLU(inplace=True),
            nn.MaxPool2d(2),
            nn.Flatten()
        )

        # Dynamic feature size calculation
        with torch.no_grad():
            dummy = torch.zeros(1, 3, patch_size, patch_size)
            dummy_out = self.features(dummy)
            in_features = dummy_out.size(1)

        self.classifier = nn.Sequential(
            nn.Linear(in_features, 256),
            nn.ReLU(inplace=True),
            nn.Dropout(0.3),
            nn.Linear(256, 2)
        )

    def forward(self, x):
        x = self.features(x)
        return self.classifier(x)

# Initialize model
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = PatchCraftDetector(patch_size=64).to(device)

# Load trained weights (update path as needed)
model_path = '/content/Cosmos_Art_Detector.pth'
model.load_state_dict(torch.load(model_path, map_location=device))
model.eval()  # Disable dropout and enable eval mode

def preprocess_image(image_bytes):
    """Convert uploaded image to normalized tensor"""
    image = Image.open(io.BytesIO(image_bytes))

    # Convert to RGB if needed
    if image.mode == 'RGBA':
        image = image.convert('RGB')
    elif image.mode == 'L':
        image = image.convert('RGB')

    image = np.array(image)
    image = cv2.resize(image, (128, 128))
    image = image.astype(np.float32) / 255.0
    image = np.transpose(image, (2, 0, 1))  # CHW format
    return image

def predict_image_stable(image_bytes, num_patches=50, seed=42):
    """Stable prediction with fixed patch locations"""
    set_seed(seed)
    img = preprocess_image(image_bytes)
    patch_size = 64
    max_pos = 128 - patch_size

    # Generate fixed patch locations
    patch_locations = [(np.random.randint(0, max_pos),
                       np.random.randint(0, max_pos))
                      for _ in range(num_patches)]

    # Extract patches
    patches = []
    for x, y in patch_locations:
        patch = img[:, x:x+patch_size, y:y+patch_size]
        patches.append(patch)

    patches = torch.tensor(np.array(patches), dtype=torch.float32).to(device)

    # Predict
    with torch.no_grad():
        outputs = model(patches)
        probs = torch.softmax(outputs, dim=1)
        ai_probs = probs[:, 1].cpu().numpy()

    confidence = np.mean(ai_probs)
    is_ai = confidence > 0.5

    return is_ai, confidence, patch_locations

# Create UI
upload = widgets.FileUpload(
    accept='image/*',
    multiple=False,
    description='Upload Image'
)

output = widgets.Output()

def on_upload_change(change):
    with output:
        output.clear_output()
        if not upload.value:
            return

        filename = next(iter(upload.value))
        image_bytes = upload.value[filename]['content']

        # Display image
        display(Image.open(io.BytesIO(image_bytes)))

        # Get prediction
        is_ai, confidence, _ = predict_image_stable(image_bytes)

        # Show results
        result = "AI-generated" if is_ai else "Human-made"
        print(f"\nClassification: {result}")
        print(f"Confidence: {confidence:.1%}")
        print("\nHow it works:")
        print("- Analyzes 50 random patches from the image")
        print("- Each patch gets a separate prediction")
        print("- Results are averaged for final score")

upload.observe(on_upload_change, names='value')

print("""AI Image Detector
Upload any image to check if it was AI-generated or human-created:""")
display(upload)
display(output)

AI Image Detector
Upload any image to check if it was AI-generated or human-created:


FileUpload(value={}, accept='image/*', description='Upload Image')

Output()